In [1]:
from data_generator.csv_data_processor import CSVDataProcessor
from utils.util_funcs import get_row_count, display_df
from pyspark.sql import SparkSession
from pyspark.sql.functions import to_date, col, floor, datediff, current_date, lower, lit, array, rand, collect_list, size, array, floor, date_add, concat, when, row_number
    

In [2]:



spark = SparkSession.builder.appName("ETL").getOrCreate()

csv_reader = CSVDataProcessor(spark, "data/healthcare_dataset.csv")

# Read the CSV file
df = csv_reader.run()


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/02/01 07:49:11 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [3]:
start_date = to_date(lit("1935-01-01"))  # Start of the date range
range_days = 365 * 90  # Number of days in the range  365 * years

df = (df.withColumn("RandomDays", (rand() * range_days).cast("int"))
        .withColumn("DOB", date_add(start_date, "RandomDays")).drop("age") 
       .withColumn("Age", floor(datediff(current_date(), col("DOB")) / 365)))




In [4]:
df.show()

+--------------------+------+----------+-----------------+-----------------+------------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+----------+----------+---+
|                name|gender|blood_type|medical_condition|date_of_admission|            doctor|            hospital|insurance_provider|    billing_amount|room_number|admission_type|discharge_date| medication|test_results|RandomDays|       DOB|Age|
+--------------------+------+----------+-----------------+-----------------+------------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+----------+----------+---+
|     Tiffany Ramirez|Female|        O-|         Diabetes|       2022-11-17|    Patrick Parker|    Wallace-Hamilton|          Medicare| 37490.98336352819|        146|      Elective|    2022-12-01|    Aspirin|Inconclusive|     18482|1985-08-08| 38|
|       

In [5]:
from constants.admission_types_tests_dataset import admission_mapping, admission_tests
# Flatten the mapping and create a DataFrame
flattened = [
    (top_level, sub_level, stay_type, admission_tests.get(sub_level, ["No tests"]))
    for top_level, sub_level_dict in admission_mapping.items()
    for sub_level, stay_types in sub_level_dict.items()
    for stay_type in stay_types
]



In [6]:
mapping_df = spark.createDataFrame(flattened, ["top_level_admission", "sub_level_admission", "stay_type", "possible_tests"])

display_df(mapping_df)

top_level_admission      sub_level_admission    stay_type  \
0            emergency               injury_rtc  day_patient   
1            emergency               injury_rtc    inpatient   
2            emergency           self_inflicted    inpatient   
3            emergency               cardiology  day_patient   
4            emergency               cardiology    inpatient   
5            emergency                neurology    inpatient   
6            emergency              pulmonology  day_patient   
7            emergency              pulmonology    inpatient   
8            emergency      infectious_diseases   outpatient   
9            emergency      infectious_diseases    inpatient   
10         gp_referral                   mental   outpatient   
11         gp_referral                   mental    inpatient   
12         gp_referral              orthopedics  day_patient   
13         gp_referral              orthopedics    inpatient   
14         gp_referral         gastroenterology  day_patient   
15         gp_referral         gastroenterology   outpatient   
16         gp_referral            endocrinology   outpatient   
17         gp_referral              dermatology   outpatient   
18         gp_referral               geriatrics   outpatient   
19         gp_referral               geriatrics    inpatient   
20   hospital_referral                   cancer  day_patient   
21   hospital_referral                   cancer    inpatient   
22   hospital_referral               nephrology    inpatient   
23   hospital_referral               cardiology  day_patient   
24   hospital_referral               cardiology    inpatient   
25   hospital_referral                neurology    inpatient   
26   hospital_referral                 oncology  day_patient   
27   hospital_referral                 oncology    inpatient   
28   hospital_referral  otorhinolaryngology_ENT  day_patient   
29   hospital_referral  otorhinolaryngology_ENT    inpatient   
30       self_referral                   mental   outpatient   
31       self_referral              dermatology   outpatient   
32       self_referral              orthopedics  day_patient   
33       self_referral         gastroenterology   outpatient   
34       self_referral            endocrinology   outpatient   
35       self_referral                 oncology  day_patient   
36       self_referral                 oncology   outpatient   
37       self_referral                 oncology    inpatient   
38            elective                maternity  day_patient   
39            elective                maternity    inpatient   
40            elective              orthopedics  day_patient   
41            elective              orthopedics    inpatient   
42            elective               obstetrics    inpatient   
43            elective            ophthalmology   outpatient   
44            elective            ophthalmology  day_patient   
45            elective               geriatrics   outpatient   
46            elective               geriatrics    inpatient   

                                       possible_tests  
0    [X-rays, CT scans, MRI, Ultrasound, Blood tests]  
1    [X-rays, CT scans, MRI, Ultrasound, Blood tests]  
2   [Psychological assessment, X-rays (for physica...  
3   [ECG, Echocardiogram, Stress tests, Cardiac ca...  
4   [ECG, Echocardiogram, Stress tests, Cardiac ca...  
5   [MRI or CT scans of the brain, Electroencephal...  
6   [Pulmonary function tests, Chest X-ray, CT sca...  
7   [Pulmonary function tests, Chest X-ray, CT sca...  
8   [Blood cultures, PCR tests, Antibody tests, Im...  
9   [Blood cultures, PCR tests, Antibody tests, Im...  
10  [Psychological evaluation, Blood tests, Brain ...  
11  [Psychological evaluation, Blood tests, Brain ...  
12   [X-rays, MRI, CT scans, Bone scans, Blood tests]  
13   [X-rays, MRI, CT scans, Bone scans, Blood tests]  
14  [Endoscopy, Colonoscopy, Blood tests, Stool te...  
15  [Endoscopy, Colonoscopy, Blood

In [7]:
# create joining column to mapping_df
admission_types = list(admission_mapping.keys())

print(admission_types)

keys_array = array([lit(key) for key in admission_types])

df = df.withColumn("top_level_admission", keys_array[floor(rand() * len(admission_types))]).drop("admission_type")


['emergency', 'gp_referral', 'hospital_referral', 'self_referral', 'elective']


In [8]:
df.show()

+--------------------+------+----------+-----------------+-----------------+------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+-------------------+
|                name|gender|blood_type|medical_condition|date_of_admission|            doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|RandomDays|       DOB|Age|top_level_admission|
+--------------------+------+----------+-----------------+-----------------+------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+-------------------+
|     Tiffany Ramirez|Female|        O-|         Diabetes|       2022-11-17|    Patrick Parker|    Wallace-Hamilton|          Medicare| 37490.98336352819|        146|    2022-12-01|    Aspirin|Inconclusive|     18482|1985-08-08| 38|  hospita

In [9]:

# Define constants and conditions
female_only = ['maternity', 'obstetrics']
is_female = lower(col('gender')) == 'female'
is_pediatric = col("Age") < 18
is_geriatric = (col("Age") >= 65) & (col("sub_level_admission") == "geriatrics")

In [10]:
from data_generator.constants import ColConstants

df = (df.withColumn("is_female", is_female)
        .withColumn("is_pediatric", is_pediatric)
        .withColumn("top_level_admission", 
                    when(col("is_pediatric"), 
                            concat(lit(ColConstants.peds), 
                                   col("top_level_admission")
                                   )
                            ).otherwise(col("top_level_admission"))
                    )
      )

In [12]:
df.show(n=9999)

+--------------------+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+--------------------+---------+------------+
|                name|gender|blood_type|medical_condition|date_of_admission|              doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|RandomDays|       DOB|Age| top_level_admission|is_female|is_pediatric|
+--------------------+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+--------------------+---------+------------+
|     Tiffany Ramirez|Female|        O-|         Diabetes|       2022-11-17|      Patrick Parker|    Wallace-Hamilton|          Medicare| 37490.98336352819|       

In [27]:
from pyspark.sql import Window

df = df.join(mapping_df, "top_level_admission", "inner")

# Define a window specification that partitions data by 'top_level_admission' (or another unique patient identifier if needed)
windowSpec = Window.partitionBy('name').orderBy(rand())

# Assign row numbers within each partition in a random order
ranked_df = df.withColumn("row_num", row_number().over(windowSpec))



In [28]:
ranked_df.show()

+-------------------+---------------+------+----------+-----------------+-----------------+-----------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+---------+------------+-------------------+-----------+--------------------+-------+
|top_level_admission|           name|gender|blood_type|medical_condition|date_of_admission|           doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|RandomDays|       DOB|Age|is_female|is_pediatric|sub_level_admission|  stay_type|      possible_tests|row_num|
+-------------------+---------------+------+----------+-----------------+-----------------+-----------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+---------+------------+-------------------+-----------+--------------------+-------+
|      

In [ ]:
# TODO filter on is pediatric, geraiatric and is_female to be done here and same people with dob? needs  to be considered 

In [29]:
# Filter to keep only the top-ranked row within each partition
ranked_df = ranked_df.filter(ranked_df.row_num == 1)

In [ ]:
# TODO row's are missing from the rank filter investigation required here
# 2500 missing or so.

In [30]:
ranked_df.show(n=8000)

+-------------------+--------------------+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+---------+------------+--------------------+-----------+--------------------+-------+
|top_level_admission|                name|gender|blood_type|medical_condition|date_of_admission|              doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|RandomDays|       DOB|Age|is_female|is_pediatric| sub_level_admission|  stay_type|      possible_tests|row_num|
+-------------------+--------------------+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+---------+------------+--------------------+-----------+----------

In [14]:
from pyspark.sql.types import StringType

df = df.select([col(c).cast(StringType()).alias(c) for c in df.columns])
df.write.csv('./temp_data/temp.csv', mode = 'overwrite', header=True)